In [ ]:
!pip install arch
!pip install yfinance

In [3]:
import yfinance as yf
import pandas as pd
import numpy as np
# gráficos interactivos
import plotly.graph_objects as go
import plotly.express as px
from arch import arch_model
# web scrapping
import bs4 as bs
import requests
import lxml
from functools import reduce
# matplotlib
import matplotlib.pyplot as plt
import seaborn as sns
sns.set()

In [4]:
def getSymbols(url):
  resp = requests.get(url)
  soup = bs.BeautifulSoup(resp.text, 'lxml')
  table = soup.find('table', {'class': 'wikitable sortable'})
  ipc_table = pd.read_html(str(table))[0]
  # extraemos símbolos
  stocks = []
  for row in ipc_table.Symbol:
    symbol = row.strip().replace(" ", "").replace("-", "").replace("&", "")  + '.MX'
    stocks.append(symbol)
  return stocks

In [5]:
def getData(stocks, start_date, end_date):
  stock_data = {}
  for stock in stocks:
    symbol = yf.Ticker(stock)
    stock_data[stock] = symbol.history(start=start_date, end=end_date)['Close']

  df = pd.DataFrame(stock_data)
  return df

In [6]:
url = 'https://en.wikipedia.org/wiki/Indice_de_Precios_y_Cotizaciones'

symbols = getSymbols(url)
data = getData(symbols, start_date='2010-01-01', end_date='2022-08-01')
data.head()

- KOFL.MX: No data found, symbol may be delisted
- LIVEPOLC1.MX: No data found for this date range, symbol may be delisted
- PEOLES.MX: No data found, symbol may be delisted
- SITESB1.MX: No data found, symbol may be delisted


AC.MX  ALFAA.MX  ALSEA.MX    AMXL.MX   ASURB.MX  BBAJIOO.MX  \
Date                                                                          
2010-01-04  26.626413  8.556671  8.968350  11.812742  51.313160         NaN   
2010-01-05  26.626413  8.383159  8.977141  11.726355  51.522839         NaN   
2010-01-06  26.503990  8.431898  8.968350  11.696304  52.694138         NaN   
2010-01-07  26.681503  8.411427  8.915595  11.854058  52.939972         NaN   
2010-01-08  26.197937  8.340268  8.915595  11.775181  52.563995         NaN   

            BIMBOA.MX  BOLSAA.MX  CEMEXCPO.MX  CUERVO.MX  ...   ORBIA.MX  \
Date                                                      ...              
2010-01-04  19.716587   8.665266    11.338881        NaN  ...  19.795584   
2010-01-05  19.739016   8.883576    11.346002        NaN  ...  20.333256   
2010-01-06  19.716587   8.978737    11.239166        NaN  ...  20.711916   
2010-01-07  19.848928   9.029119    11.331758        NaN  ...  21.537359   
2010-01-08  19.739016   9.499324    11.217799        NaN  ...  21.590366   

            PEOLES.MX  PINFRA.MX  Q.MX  RA.MX  SITESB1.MX  TLEVISACPO.MX  \
Date                                                                       
2010-01-04        NaN  25.662481   NaN    NaN         NaN      51.064980   
2010-01-05        NaN  25.653690   NaN    NaN         NaN      50.371109   
2010-01-06        NaN  26.365562   NaN    NaN         NaN      49.892895   
2010-01-07        NaN  26.356773   NaN    NaN         NaN      50.680534   
2010-01-08        NaN  26.488602   NaN    NaN         NaN      49.517838   

            VESTA.MX  VOLARA.MX  WALMEX.MX  
Date                                        
2010-01-04       NaN        NaN  22.888065  
2010-01-05       NaN        NaN  23.286453  
2010-01-06       NaN        NaN  23.363068  
2010-01-07       NaN        NaN  22.895729  
2010-01-08       NaN        NaN  22.715693  

[5 rows x 35 columns]

In [7]:
len(data.columns)

35

In [8]:
data = data[[data.columns[i] for i in range(len(data.columns)) if ~np.isnan(data.iloc[0][i]) ]]
data.head()

AC.MX  ALFAA.MX  ALSEA.MX    AMXL.MX   ASURB.MX  BIMBOA.MX  \
Date                                                                         
2010-01-04  26.626413  8.556671  8.968350  11.812742  51.313160  19.716587   
2010-01-05  26.626413  8.383159  8.977141  11.726355  51.522839  19.739016   
2010-01-06  26.503990  8.431898  8.968350  11.696304  52.694138  19.716587   
2010-01-07  26.681503  8.411427  8.915595  11.854058  52.939972  19.848928   
2010-01-08  26.197937  8.340268  8.915595  11.775181  52.563995  19.739016   

            BOLSAA.MX  CEMEXCPO.MX  ELEKTRA.MX  FEMSAUBD.MX  ...  GMEXICOB.MX  \
Date                                                         ...                
2010-01-04   8.665266    11.338881  604.178101    51.199028  ...    19.616526   
2010-01-05   8.883576    11.346002  596.843018    49.648502  ...    19.541487   
2010-01-06   8.978737    11.239166  594.830688    50.054031  ...    19.791618   
2010-01-07   9.029119    11.331758  615.613281    50.865067  ...    19.897921   
2010-01-08   9.499324    11.217799  633.499268    50.173298  ...    19.747852   

            GRUMAB.MX  KIMBERA.MX    LABB.MX  MEGACPO.MX    OMAB.MX  \
Date                                                                  
2010-01-04  20.370739   11.053910  13.846370   21.217123  10.988792   
2010-01-05  20.533363   11.023732  14.266230   21.967037  10.959105   
2010-01-06  21.183849   11.029392  14.672546   22.035210  11.013532   
2010-01-07  22.852886   10.835164  14.785411   21.936735  11.147119   
2010-01-08  23.349316   10.672997  14.762838   21.982185  11.246074   

             ORBIA.MX  PINFRA.MX  TLEVISACPO.MX  WALMEX.MX  
Date                                                        
2010-01-04  19.795584  25.662481      51.064980  22.888065  
2010-01-05  20.333256  25.653690      50.371109  23.286453  
2010-01-06  20.711916  26.365562      49.892895  23.363068  
2010-01-07  21.537359  26.356773      50.680534  22.895729  
2010-01-08  21.590366  26.488602      49.517838  22.715693  

[5 rows x 25 columns]

In [62]:
data.isna().sum()

AC.MX             3
ALFAA.MX          8
ALSEA.MX          3
AMXL.MX           3
ASURB.MX          3
BIMBOA.MX         3
BOLSAA.MX         3
CEMEXCPO.MX       3
ELEKTRA.MX        3
FEMSAUBD.MX       3
GAPB.MX          11
GCARSOA1.MX       3
GCC.MX           87
GFINBURO.MX       3
GFNORTEO.MX       3
GMEXICOB.MX       3
GRUMAB.MX         3
KIMBERA.MX        8
LABB.MX           3
MEGACPO.MX        4
OMAB.MX           3
ORBIA.MX          3
PINFRA.MX         3
TLEVISACPO.MX     3
WALMEX.MX         3
dtype: int64

In [63]:
data = data.drop('GCC.MX', axis=1)
data.head()

AC.MX  ALFAA.MX  ALSEA.MX    AMXL.MX   ASURB.MX  BIMBOA.MX  \
Date                                                                         
2010-01-04  26.626408  8.556668  8.968350  11.812745  51.313160  19.716587   
2010-01-05  26.626408  8.383159  8.977142  11.726354  51.522831  19.739017   
2010-01-06  26.503988  8.431897  8.968350  11.696303  52.694141  19.716587   
2010-01-07  26.681499  8.411427  8.915595  11.854060  52.939964  19.848925   
2010-01-08  26.197937  8.340266  8.915595  11.775184  52.563995  19.739017   

            BOLSAA.MX  CEMEXCPO.MX  ELEKTRA.MX  FEMSAUBD.MX  ...  GMEXICOB.MX  \
Date                                                         ...                
2010-01-04   8.665265    11.338881  604.178101    51.199032  ...    19.616528   
2010-01-05   8.883576    11.346002  596.843140    49.648510  ...    19.541487   
2010-01-06   8.978738    11.239166  594.830688    50.054031  ...    19.791616   
2010-01-07   9.029117    11.331758  615.613159    50.865074  ...    19.897923   
2010-01-08   9.499325    11.217799  633.499268    50.173286  ...    19.747845   

            GRUMAB.MX  KIMBERA.MX    LABB.MX  MEGACPO.MX    OMAB.MX  \
Date                                                                  
2010-01-04  20.370733   11.053907  13.846370   21.217127  10.988795   
2010-01-05  20.533358   11.023732  14.266230   21.967035  10.959106   
2010-01-06  21.183857   11.029392  14.672546   22.035210  11.013530   
2010-01-07  22.852884   10.835166  14.785412   21.936737  11.147116   
2010-01-08  23.349314   10.672996  14.762839   21.982185  11.246075   

             ORBIA.MX  PINFRA.MX  TLEVISACPO.MX  WALMEX.MX  
Date                                                        
2010-01-04  19.795588  25.662483      51.064980  22.888071  
2010-01-05  20.333263  25.653694      50.371105  23.286455  
2010-01-06  20.711910  26.365561      49.892902  23.363073  
2010-01-07  21.537352  26.356775      50.680531  22.895729  
2010-01-08  21.590368  26.488602      49.517830  22.715689  

[5 rows x 24 columns]

In [9]:
data_fill = data.interpolate()
data_fill.isna().sum()

AC.MX            0
ALFAA.MX         0
ALSEA.MX         0
AMXL.MX          0
ASURB.MX         0
BIMBOA.MX        0
BOLSAA.MX        0
CEMEXCPO.MX      0
ELEKTRA.MX       0
FEMSAUBD.MX      0
GAPB.MX          0
GCARSOA1.MX      0
GCC.MX           0
GFINBURO.MX      0
GFNORTEO.MX      0
GMEXICOB.MX      0
GRUMAB.MX        0
KIMBERA.MX       0
LABB.MX          0
MEGACPO.MX       0
OMAB.MX          0
ORBIA.MX         0
PINFRA.MX        0
TLEVISACPO.MX    0
WALMEX.MX        0
dtype: int64

In [10]:
date_bottons = [
    {'count':1, 'label':"1M", 'step':"month", 'stepmode':"backward"},
    {'count':6, 'label':"6M", 'step':"month", 'stepmode':"backward"},
    {'count':1, 'label':"1YR", 'step':"year", 'stepmode':"backward"},
    {'count':5, 'label':"5YR", 'step':"year", 'stepmode':"backward"},
    {'step':"all"}
    ]

fig = go.Figure()
for stock in data_fill.columns:
  fig.add_trace(go.Scatter(
      x = data_fill.reset_index()['Date'],
      y = data_fill.reset_index()[stock],
      mode = 'lines',
      #fill='tozeroy',
      #line_color='blue',
      name = stock))

fig.update_layout(
    {'title': {'text': 'Precios de cierre',
               'x' : 0.5, 'y': 0.9}},
    width=1200,
    height=600
)
# time bottons
fig.update_layout(
    {'xaxis': {'rangeselector': 
               {'buttons': date_bottons}
    }}
)
fig.show()

In [33]:
x_data = data_fill.columns

y_data = [data_fill[stock].tolist() for stock in data_fill.columns] 

colors = ['rgba({}, 164, 214, 0.5)'.format(i) for i in range(len(data_fill.columns))]


fig = go.Figure()

for xd, yd, cls in zip(x_data, y_data, colors):

  fig.add_trace(go.Box(
      y=yd,
      name=xd,
      boxpoints='outliers',
      #jitter=0,
      whiskerwidth=0.2,
      #fillcolor=cls,
      marker_size=2,
      line_width=1
      #marker_color=cls
      )
  )

fig.update_layout(
    title='Points Scored by the Top 9 Scoring NBA Players in 2012',
    yaxis=dict(
        #autorange=True,
        #showgrid=True,
        zeroline=True,
        #dtick=1,
        gridcolor='rgb(255, 255, 255)',
        gridwidth=1,
        zerolinecolor='rgb(255, 255, 255)',
        zerolinewidth=2,
    ),
    
    #paper_bgcolor='rgb(243, 243, 243)',
    #plot_bgcolor='rgb(243, 243, 243)',
    showlegend=False
)

fig.update_traces(orientation='v')

fig.show()

# **Rendimientos**

In [45]:
# Función para obtener los rendimientos 
def getReturns(data, simple=False):
  if simple:
    ret = data/data.shift(1) -1
  else:
    ret = np.log(data/data.shift(1))
  return ret.dropna()

In [46]:
returns = getReturns(data_fill, simple=True)
returns.head()

AC.MX  ALFAA.MX  ALSEA.MX   AMXL.MX  ASURB.MX  BIMBOA.MX  \
Date                                                                      
2010-01-05  0.000000 -0.020278  0.000980 -0.007313  0.004086   0.001138   
2010-01-06 -0.004598  0.005814 -0.000979 -0.002563  0.022734  -0.001136   
2010-01-07  0.006698 -0.002428 -0.005882  0.013488  0.004665   0.006712   
2010-01-08 -0.018124 -0.008460  0.000000 -0.006654 -0.007102  -0.005537   
2010-01-11 -0.026869  0.017999 -0.015779  0.012759 -0.028473   0.027614   

            BOLSAA.MX  CEMEXCPO.MX  ELEKTRA.MX  FEMSAUBD.MX  ...  GMEXICOB.MX  \
Date                                                         ...                
2010-01-05   0.025194     0.000628   -0.012141    -0.030284  ...    -0.003825   
2010-01-06   0.010712    -0.009416   -0.003372     0.008168  ...     0.012800   
2010-01-07   0.005611     0.008238    0.034939     0.016203  ...     0.005371   
2010-01-08   0.052077    -0.010057    0.029054    -0.013600  ...    -0.007542   
2010-01-11  -0.027106     0.001905    0.034929    -0.130903  ...     0.004433   

            GRUMAB.MX  KIMBERA.MX   LABB.MX  MEGACPO.MX   OMAB.MX  ORBIA.MX  \
Date                                                                          
2010-01-05   0.007983   -0.002730  0.030323    0.035345 -0.002702  0.027161   
2010-01-06   0.031679    0.000513  0.028481    0.003103  0.004966  0.018623   
2010-01-07   0.078788   -0.017610  0.007692   -0.004469  0.012129  0.039854   
2010-01-08   0.021723   -0.014967 -0.001527    0.002072  0.008877  0.002461   
2010-01-11  -0.015396   -0.022968 -0.023853    0.004480 -0.012319  0.009470   

            PINFRA.MX  TLEVISACPO.MX  WALMEX.MX  
Date                                             
2010-01-05  -0.000343      -0.013588   0.017406  
2010-01-06   0.027749      -0.009494   0.003290  
2010-01-07  -0.000333       0.015787  -0.020003  
2010-01-08   0.005002      -0.022942  -0.007863  
2010-01-11  -0.023557      -0.003787   0.025126  

[5 rows x 25 columns]

In [67]:
date_bottons = [
    {'count':1, 'label':"1M", 'step':"month", 'stepmode':"backward"},
    {'count':6, 'label':"6M", 'step':"month", 'stepmode':"backward"},
    {'count':1, 'label':"1YR", 'step':"year", 'stepmode':"backward"},
    {'count':5, 'label':"5YR", 'step':"year", 'stepmode':"backward"},
    {'step':"all"}
    ]

fig = go.Figure()
for stock in ['ELEKTRA.MX']:
  fig.add_trace(go.Scatter(
      x = returns.reset_index()['Date'],
      y = returns[stock],
      mode = 'lines',
      #fill='tozeroy',
      #line_color='blue',
      name = stock))

fig.update_layout(
    {'title': {'text': 'Rendimientos',
               'x' : 0.5, 'y': 0.9}},
    width=1200,
    height=600
)
# time bottons
fig.update_layout(
    {'xaxis': {'rangeselector': 
               {'buttons': date_bottons}
    }}
)
fig.show()

# **GARCH Model**

In [102]:
# especificación del modelo GARCH(1, 1)
model = arch_model(returns['ELEKTRA.MX'], p = 1, q = 1, mean = 'constant', vol = 'GARCH', dist = 'normal')
# actualiza el modelo cada 4 iteraciones
res = model.fit(update_freq=4)

Iteration:      4,   Func. Count:     46,   Neg. LLF: -8668.878825838157
Optimization terminated successfully    (Exit mode 0)
            Current function value: -8668.878809725842
            Iterations: 8
            Function evaluations: 46
            Gradient evaluations: 4


/usr/local/lib/python3.7/dist-packages/arch/univariate/base.py:310: DataScaleWarning:

y is poorly scaled, which may affect convergence of the optimizer when
estimating the model parameters. The scale of y is 0.0004198. Parameter
estimation work better when this value is between 1 and 1000. The recommended
rescaling is 100 * y.

This warning can be disabled by either rescaling y before initializing the
model or by setting rescale=False.




Prámetros estimados por máxima verosimilitud.

In [103]:
print(res.summary())

                     Constant Mean - GARCH Model Results                      
Dep. Variable:             ELEKTRA.MX   R-squared:                       0.000
Mean Model:             Constant Mean   Adj. R-squared:                  0.000
Vol Model:                      GARCH   Log-Likelihood:                8668.88
Distribution:                  Normal   AIC:                          -17329.8
Method:            Maximum Likelihood   BIC:                          -17305.5
                                        No. Observations:                 3158
Date:                Sun, Sep 04 2022   Df Residuals:                     3157
Time:                        17:54:08   Df Model:                            1
                                 Mean Model                                 
                 coef    std err          t      P>|t|      95.0% Conf. Int.
----------------------------------------------------------------------------
mu         1.6225e-04  4.354e-06     37.262 6.723e-304 [1.

In [118]:
volatility_sup = res.conditional_volatility
volatility_inf = -res.conditional_volatility
volatility_inf

Date
2010-01-05   -0.022764
2010-01-06   -0.021044
2010-01-07   -0.018877
2010-01-08   -0.022983
2010-01-11   -0.024235
                ...   
2022-07-25   -0.019593
2022-07-26   -0.017801
2022-07-27   -0.016746
2022-07-28   -0.015116
2022-07-29   -0.014082
Name: cond_vol, Length: 3158, dtype: float64

In [121]:
date_bottons = [
    {'count':1, 'label':"1M", 'step':"month", 'stepmode':"backward"},
    {'count':6, 'label':"6M", 'step':"month", 'stepmode':"backward"},
    {'count':1, 'label':"1YR", 'step':"year", 'stepmode':"backward"},
    {'count':5, 'label':"5YR", 'step':"year", 'stepmode':"backward"},
    {'step':"all"}
    ]

fig = go.Figure()
for stock in ['ELEKTRA.MX']:
  fig.add_trace(go.Scatter(
      x = returns.reset_index()['Date'],
      y = returns[stock],
      mode = 'lines',
      #fill='tozeroy',
      line_color='blue',
      name = stock))

fig.add_trace(go.Scatter(
      x = returns.reset_index()['Date'],
      y = volatility_sup.tolist(),
      mode = 'lines',
      #fill='tozeroy',
      line_color='red',
      name = 'volatility'))

fig.add_trace(go.Scatter(
      x = returns.reset_index()['Date'],
      y = volatility_inf.tolist(),
      mode = 'lines',
      #fill='tozeroy',
      line_color='red',
      name = 'volatility'))

fig.update_layout(
    {'title': {'text': 'Rendimientos',
               'x' : 0.5, 'y': 0.9}},
    width=1200,
    height=600
)
# time bottons
fig.update_layout(
    {'xaxis': {'rangeselector': 
               {'buttons': date_bottons}
    }}
)
fig.show()

# **Residuales**

In [160]:
residuales = res.resid

In [164]:
fig = go.Figure()
fig.add_trace(go.Histogram(x=residuales, name = 'volatility'))
fig.update_layout(
    {'title': {'text': 'Hostograma de los Rendimientos',
               'x' : 0.5, 'y': 0.9}},
    width=1200,
    height=600
)
fig.show()

# **Forecasting**

In [171]:
# Make 5-period ahead forecast
model_forecast = res.forecast(horizon = 10)
# Print out the last row of variance forecast
print(model_forecast.variance[-1:])

                h.01      h.02      h.03    h.04      h.05      h.06  \
Date                                                                   
2022-07-29  0.000186  0.000191  0.000195  0.0002  0.000204  0.000209   

                h.07      h.08      h.09      h.10  
Date                                                
2022-07-29  0.000213  0.000217  0.000221  0.000225  


/usr/local/lib/python3.7/dist-packages/arch/__future__/_utility.py:21: FutureWarning:


The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.




In [175]:
forecast = model_forecast.variance.dropna().values.flatten()
print(np.sqrt(forecast))


[0.01364545 0.01381557 0.01398028 0.01413983 0.01429446 0.01444439
 0.01458983 0.01473097 0.01486798 0.01500104]
